# Sujet 6 : Autour du Paradoxe de Simpson

In [88]:
%matplotlib inline
import matplotlib.pyplot as plt
import pandas as pd

In [89]:
# get data
data_url = "https://gitlab.inria.fr/learninglab/mooc-rr/mooc-rr-ressources/-/raw/master/module3/Practical_session/Subject6_smoking.csv"

raw_data = pd.read_csv(data_url)
raw_data

Smoker Status   Age
0       Yes  Alive  21.0
1       Yes  Alive  19.3
2        No   Dead  57.5
3        No  Alive  47.1
4       Yes  Alive  81.4
5        No  Alive  36.8
6        No  Alive  23.8
7       Yes   Dead  57.5
8       Yes  Alive  24.8
9       Yes  Alive  49.5
10      Yes  Alive  30.0
11       No   Dead  66.0
12      Yes  Alive  49.2
13       No  Alive  58.4
14       No   Dead  60.6
15       No  Alive  25.1
16       No  Alive  43.5
17       No  Alive  27.1
18       No  Alive  58.3
19      Yes  Alive  65.7
20       No   Dead  73.2
21      Yes  Alive  38.3
22       No  Alive  33.4
23      Yes   Dead  62.3
24       No  Alive  18.0
25       No  Alive  56.2
26      Yes  Alive  59.2
27       No  Alive  25.8
28       No   Dead  36.9
29       No  Alive  20.2
...     ...    ...   ...
1284    Yes   Dead  36.0
1285    Yes  Alive  48.3
1286     No  Alive  63.1
1287     No  Alive  60.8
1288    Yes   Dead  39.3
1289     No  Alive  36.7
1290     No  Alive  63.8
1291     No   Dead  71.3
1292     No  Alive  57.7
1293     No  Alive  63.2
1294     No  Alive  46.6
1295    Yes   Dead  82.4
1296    Yes  Alive  38.3
1297    Yes  Alive  32.7
1298     No  Alive  39.7
1299    Yes   Dead  60.0
1300     No   Dead  71.0
1301     No  Alive  20.5
1302     No  Alive  44.4
1303    Yes  Alive  31.2
1304    Yes  Alive  47.8
1305    Yes  Alive  60.9
1306     No   Dead  61.4
1307    Yes  Alive  43.0
1308     No  Alive  42.1
1309    Yes  Alive  35.9
1310     No  Alive  22.3
1311    Yes   Dead  62.1
1312     No   Dead  88.6
1313     No  Alive  39.1

[1314 rows x 3 columns]

## 1. taux de mortalité en fonction de leur habitude de tabagisme

In [47]:
# data[i] i=0: non-smoker, i=1 smoker
# data[i][j] j=0: alive, j=1 dead
data = [[0, 0], [0, 0]]
NONSMOKER, SMOKER = (0, 1)
ALIVE, DEAD = (0, 1)

for _, e in raw_data.iterrows(): 
    data[e["Smoker"]=="Yes"][e["Status"]=="Dead"] += 1

# mortality_rate = (%dead among non-smokers), (%dead among smokers)
mortality_rate = [
    data[NONSMOKER][DEAD]/sum(data[NONSMOKER])*100,
    data[SMOKER][DEAD]/sum(data[SMOKER])*100
]

pd.DataFrame(mortality_rate, columns=[""], index=["taux de décès parmi les non-fumeurs (%)", "taux de décès parmi les fumeurs (%)"])

taux de décès parmi les non-fumeurs (%)  31.420765
taux de décès parmi les fumeurs (%)      23.883162

Conclusion: Il y a plus de morts parmi les non-fumeurs. Ne pas fumer serait dangereux ?
    
## 2. taux de mortalité en fonction de l'age et l'habitude de tabagisme

In [52]:
age_categories = ["18-34 ans", "34-54 ans", "55-64 ans", "65+ ans"]
# data[age][is smoking][is dead] = nb people
data = [ [[0, 0], [0, 0]] for a in age_categories ]

for _, e in raw_data.iterrows():
    age = 0
    if e["Age"] > 34 and e["Age"] <= 54:
        age = 1
    elif e["Age"] > 55 and e["Age"] <= 64:
        age = 2
    elif e["Age"] > 64:
        age = 3
    data[age][e["Smoker"]=="Yes"][e["Status"]=="Dead"] += 1

mortality_rate = [[
    e[NONSMOKER][DEAD]/sum(e[NONSMOKER])*100,
    e[SMOKER][DEAD]/sum(e[SMOKER])*100
] for e in data]
    
pd.DataFrame(mortality_rate, index=age_categories, columns=["taux de décès parmi les non-fumeurs (%)", "taux de décès parmi les fumeurs (%)"])

taux de décès parmi les non-fumeurs (%)  \
18-34 ans                                 2.739726   
34-54 ans                                 9.547739   
55-64 ans                                33.057851   
65+ ans                                  85.492228   

           taux de décès parmi les fumeurs (%)  
18-34 ans                             3.296703  
34-54 ans                            17.299578  
55-64 ans                            43.859649  
65+ ans                              85.714286

Conclusion: il y a moins de décès chez les non-fumeurs indépendament de leur catégorie d'age.

Ce qui semble contredire le résultat précédent ? Pas forcément. Pour y voir plus clair, étudions le nombre de fumeurs en fonction de leur catégorie d'age.



In [58]:
nb = [[
    sum(e[NONSMOKER]), sum(e[SMOKER])
] for e in data]

pd.DataFrame(nb, index=age_categories, columns=["nb non-fumeurs", "nb fumeurs"])

nb non-fumeurs  nb fumeurs
18-34 ans             219         182
34-54 ans             199         237
55-64 ans             121         114
65+ ans               193          49

On remarque le piège ! La plupart des personnes de 65+ ans ne fument pas (~75%) ! Mais ont le plus grand taux de décès, indépendament du fait qu'elles fument. En aggrégant les catégories d'age, elles font remonter énormément le nombre de décès parmi les non-fumeurs et peu parmi les non-fumeurs. D'où le fait qu'on observe un taux de décès parmi les non-fumeurs plus important.